In [ ]:
#soundtrack - a datetime based music player
from soundtrack import *
import time
import sqlite3
from IPython.display import clear_output
import IPython
from datetime import datetime, timedelta
import pickle
import datetime as dt

db="soundtrack.db"
filename='music_dict.p'
buffer_sleep=0 #use if laggy connection to prevent STs from get skipped.
update_bit=0
#remove pickle stuff asap. TODO: rewrite cronjob to only look for songs not in db then add. 
#then eventually put that functionality into the program
#pickle will have new shuffle songs, but use only when necessary because only created four times per day 
#and will have songs already heard today in many cases.
#try:
#    music_dict=music_dict
#    print("*******No pickle needed*********")
#except:
#    print("*******Pickle needed*********")
#    pickle=pickle.load(open(filename,"rb"))
#    music_dict=pickle
try:
    music_dict=music_dict
    print("*******No DB call needed*********")
except:
    print("*******DB call needed*********")
    music_dict=getMusicDicts()    
while datetime.now().hour < 24:
    for song in music_dict:
        b=song[1][2]
        current_datetime=datetime.now().strftime('%A %H:%M:%S')
        #b=float(getMediaDuration(song[0]))
        print("Current Time:{}".format(current_datetime))
        table='song_schedule'
        current_dow=datetime.now().strftime('%w')
        current_time=datetime.now().strftime('%H:%M:%S')
        statement="SELECT * FROM {} WHERE dow='{}' AND time >'{}' ORDER BY dow ASC, time ASC LIMIT 0,1".format(table,current_dow,current_time)
        con = sqlite3.connect(db)
        cursor=con.execute(statement)
        rows = cursor.fetchall()
        for row in rows:
            next_song_time=datetime.strptime(row[1],'%H:%M:%S').time()
        song_dt = dt.datetime.combine(dt.date.today(), next_song_time)
        now=dt.datetime.now()
        difference=song_dt-now
        difference=difference.seconds
        print("{} seconds until next Soundtrack song.".format(difference))
        #time algos
        if difference < 60: #play ST song
            #build db update here instead of cronjob built. testing 20190821
            #if difference > 20 seconds and the db hasn't been updated then update the db
            print("Difference is :{}".format(difference))
            if (difference > 20): #add update bit conditinal once the below proves working 20190821
                print("!!!!!!!!!!!!!!!Opportunity to do add new songs to DB!!!!!!!!!!!!")
                new_files=getDBStatus()
                print(new_files)
                print("Update bit: {}".format(update_bit))
                if new_files:
                    addToDB()
                update_bit=1
            getNearbySchedule(current_dow,current_time)
            print("Less than 60 seconds")
            time.sleep(difference/2) #play sooner. maybe /2 half if sometimes wait seems tooo long
            song="/home/pi/Music/"+row[2]
            b=float(getMediaDuration(song))
            print("Now Playing SoundTrack \n  {} is {} seconds.".format(song,b))
            IPython.display.display(IPython.display.Audio(song,autoplay=True, embed=None))            
            time.sleep(b+buffer_sleep+2) #an additional 2 seconds for STs to play until the end
            clear_output()
            break
        elif difference < 300: #find a shuffle song that fits this short gap before next ST
            if 1 < difference-b <= 15:
                getNearbySchedule(current_dow,current_time)
                music_dict.remove(song) #remove shuffle song about to play so that next time start program it skips
                IPython.display.display(IPython.display.Audio(song[0],autoplay=True, embed=None))
                print("Now Playing(pre-SoundTrack): {} : {} seconds : ".format(getMediaName(song[0]),b), end="")
                next_tm = datetime.now() + timedelta(0,float(b))
                print("Ends @ {}".format(next_tm.time()))
                statement=getShuffleCountExists(song[0])
                print(statement)
                con.execute(statement)
                con.commit()
                con.close()
                time.sleep(b+buffer_sleep)
                clear_output()
                break
        elif b < difference: #play shuffle song  
            music_dict.remove(song)
            getNearbySchedule(current_dow,current_time)
            IPython.display.display(IPython.display.Audio(song[0],autoplay=True, embed=None))
            print("Now Playing: {} : {} seconds : ".format(getMediaName(song[0]),b), end="")
            next_tm = datetime.now() + timedelta(0,float(b))
            print("Ends @ {}".format(next_tm.time()))
            statement=getShuffleCountExists(song[0])
            print(statement)
            con.execute(statement)
            con.commit()
            con.close()
            time.sleep(b+buffer_sleep)
        clear_output()

Current Time:Wednesday 16:27:54
125 seconds until next Soundtrack song.
15:45:00: it_s_all_understood_lyrics_Jack_Johnson.mp3
15:52:30: Pete_Yorn-For Us.mp3
16:00:00: Beck-Elevator_Music.mp3
16:15:00: AFlockOfSeagulls-SpaceAgeLoveSong.mp3
Next: 16:30:00: go_betweens-StreetsofYourTown.mp3
16:37:30: shuffle_exclude/Go On.mp3
16:45:00: BlackCrowes_unplugged_Sting_Me.mp3
17:00:00: bruce_springsteen-sad_eyes.mp3
17:15:00: JackJohnson-Matt Costa-ZachGill-LetItBeSung.mp3


Now Playing(pre-SoundTrack): The_Smiths_-_Please_Please_Please_Let_Me_Get_What_I_Want.mp3 : 113 seconds : Ends @ 16:29:48.011154
UPDATE shuffle_count SET cnt=31,time="2019-08-21 16:27:55" WHERE name="/home/pi/Music/The_Smiths_-_Please_Please_Please_Let_Me_Get_What_I_Want.mp3"


In [ ]:
print(music_dict)